In [1]:
import os
os.getcwd()

'c:\\Users\\Alex\\Documents\\repos\\Predicting-ATP-Tennis-Match-Outcomes\\Python'

In [3]:
import os 
os.chdir('Temp data')


In [33]:
import pandas as pd
import numpy as np
matches = pd.concat([pd.read_csv('y_train.csv', sep = ","),pd.read_csv('X_train.csv', sep = ",")],axis = 1)
matches = matches.sort_values(['tourney_date','round'], ascending=[False, True])
matches['winner_name'] = np.where(matches['Outcome'] == 1, matches['Main_player_name'],
                                           matches['Other_player_name'])
matches['loser_name'] = np.where(matches['Outcome'] == 0, matches['Main_player_name'],
                                           matches['Other_player_name'])
matches = matches[["winner_name", "loser_name", "tourney_level", "tourney_date", "round"]]
matches.head(5)

winner_name           loser_name tourney_level  tourney_date  round
1243       Dan Martin      Joseph Phillips            15      20240520    3.0
1985      Corey Craig       Kaipo Marshall            15      20240520    3.0
3521   Alexandre Reco  Alexander Zgirovsky            25      20240520    3.0
5633    Sasa Markovic        Razvan Baiant            15      20240520    3.0
6928  Gabriel Decamps         Marino Jakic            15      20240520    3.0

In [35]:

first_date = pd.to_datetime("1900-01-01")
#matches["tourney_date"] = pd.to_datetime(matches["tourney_date"], format="%Y%m%d", origin="1900/01/01")

matches = matches.sort_values(by=["tourney_date", "round"])
matches.head(5)

winner_name         loser_name tourney_level  tourney_date  \
341            Andre Ghem    Clayton Almeida             S      20091228   
29928       Danilo Ferraz     Joao Wiesinger             S      20091228   
59170    Juan Pablo Amado  Paris Gemouchidis             S      20091228   
73637     Franco Ferreiro     Ricardo Siggia             S      20091228   
122511  Guillermo Alcaide   Damian Guichonet             S      20091228   

        round  
341       3.0  
29928     3.0  
59170     3.0  
73637     3.0  
122511    3.0

In [36]:
import random
test = matches.sample(frac=0.0001)
test.shape

(28, 5)

In [37]:

players_to_elo = {}
matches_count = {}

def compute_elo():
    matches.apply(update_matches_count_by_row, axis=1)
    matches.apply(compute_elo_by_row, axis=1)
    return players_to_elo

def compute_elo_by_row(row):
    update_elo(players_to_elo, row[0], row[1], row[0], row[2], row[3], row[4])
    return 0

def update_matches_count_by_row(row):
    update_matches_count(row[0], row[1])
    return 0

def update_matches_count(player_a, player_b):
    if player_a not in matches_count:
        matches_count[player_a] = 0
    if player_b not in matches_count:
        matches_count[player_b] = 0
    matches_count[player_a] += 1
    matches_count[player_b] += 1

def update_elo(pl_to_elo, player_a, player_b, winner, level, match_date, match_num):
    r_a = pl_to_elo.get(player_a, {"ranking": [1500], "date": [first_date], "num": [0]})["ranking"][-1]
    r_b = pl_to_elo.get(player_b, {"ranking": [1500], "date": [first_date], "num": [0]})["ranking"][-1]

    e_a = 1 / (1 + 10 ** ((r_b - r_a) / 400))
    e_b = 1 / (1 + 10 ** ((r_a - r_b) / 400))

    if winner == player_a:
        s_a = 1
        s_b = 0
    else:
        s_a = 0
        s_b = 1

    k_a = 250 / ((matches_count[player_a] + 5) ** 0.4)
    k_b = 250 / ((matches_count[player_b] + 5) ** 0.4)
    k = 1.1 if level == "G" else 1

    r_a_new = r_a + (k * k_a) * (s_a - e_a)
    r_b_new = r_b + (k * k_b) * (s_b - e_b)

    pl_to_elo[player_a] = {"ranking": pl_to_elo.get(player_a, {"ranking": [1500], "date": [first_date], "num": [0]})["ranking"] + [r_a_new],
                           "date": [match_date],
                           "num": pl_to_elo.get(player_a, {"ranking": [1500], "date": [first_date], "num": [0]})["num"] + [match_num]}
    
    pl_to_elo[player_b] = {"ranking": pl_to_elo.get(player_b, {"ranking": [1500], "date": [first_date], "num": [0]})["ranking"] + [r_b_new],
                           "date": [match_date],
                           "num": pl_to_elo.get(player_b, {"ranking": [1500], "date": [first_date], "num": [0]})["num"] + [match_num]}



In [38]:
compute_elo()

{'Andre Ghem': {'ranking': [1500,
   1512.9049662305551,
   1500.021243003395,
   1487.1154877337992,
   1474.6888778393823,
   1462.7223950466926,
   1451.7439998626257,
   1444.2930761406203,
   1433.638238600804,
   1447.9765829109886,
   1437.668761442997,
   1451.1450254117299,
   1441.0520553745973,
   1455.828718280426,
   1447.095238182867,
   1439.7570541611824,
   1451.4467803703826,
   1465.0422885966148,
   1478.7562389260127,
   1496.3737552832017,
   1505.650505177763,
   1517.8459208867146,
   1506.008691931643,
   1517.8039219088803,
   1530.6322937567088,
   1542.8009778882124,
   1534.5970229776296,
   1542.0920910439834,
   1559.1419251558234,
   1572.0739166760143,
   1585.0698868785053,
   1591.408996379983,
   1575.7605978863032,
   1585.000237100784,
   1595.0304170963368,
   1609.3529573818005,
   1624.8508667782176,
   1631.537656940043,
   1636.8654911784583,
   1618.6181006941874,
   1608.6210735966288,
   1621.0525118732226,
   1632.7367068804044,
   1619.70

In [ ]:
roger = players_to_elo["Roger Federer"]
roger = roger[roger["date"] > pd.to_datetime("2001-01-01")]

import matplotlib.pyplot as plt

plt.plot(roger["date"], roger["ranking"])
plt.xlabel("Date")
plt.ylabel("Ranking")
plt.title("Novak Djokovic's Elo Ranking Over Time")
plt.show()